In [2]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
import yfinance as yf
from finta import TA
from sklearn import svm
from sklearn.preprocessing import StandardScaler
from pandas.tseries.offsets import DateOffset
from sklearn.metrics import classification_report

In [3]:
# The trading algorithm will be tested and evaluated over three timelines:

# dcb = Dot Com Bubble
dcb_start = '1997-06-01'
dcb_end = '2002-12-01'

# crsh = 2008 Crash
crsh_start = '2007-06-01'
crsh_end = '2012-12-01'

# cvd = COVID-19
cvd_start = '2020-03-01'
cvd_end = '2022-06-01'


In [4]:
# Get price data from Yahoo! Finance for S&P 500, NASDAQ 100, and RUSSELL 2000
price_data = yf.download(
    '^GSPC ^NDX ^RUT', 
    start=dcb_start,
    end=cvd_end
)

# rename columns from tickers to descriptive names
price_data.rename(
    columns={
        '^NDX': 'NASDAQ 100',
        '^RUT': 'RUSSELL 2000',
        '^GSPC': 'SP 500', 
    },
    inplace=True
)

price_data.columns = price_data.columns.swaplevel(0, 1)
price_data = price_data.sort_index(axis='columns')
price_data.drop('Adj Close', axis='columns', level=1, inplace=True)
price_data.dropna(inplace=True)

[*********************100%***********************]  3 of 3 completed


In [5]:
# Preview the data
display(price_data.head())

NASDAQ 100                                                 \
                 Close        High         Low        Open     Volume   
Date                                                                    
1997-06-02  958.690002  967.900024  950.950012  958.849976  555220000   
1997-06-03  929.809998  958.690002  929.479980  958.690002  586410000   
1997-06-04  921.960022  941.989990  915.960022  929.809998  594220000   
1997-06-05  930.609985  935.750000  921.960022  921.960022  560950000   
1997-06-06  944.989990  946.270020  926.979980  930.609985  586010000   

           RUSSELL 2000                                                 \
                  Close        High         Low        Open     Volume   
Date                                                                     
1997-06-02   383.519989  383.540009  380.589996  380.760010  435950000   
1997-06-03   383.279999  383.720001  382.089996  383.519989  527120000   
1997-06-04   382.670013  383.350006  381.839996  383.279999  466690000   
1997-06-05   384.989990  385.000000  382.670013  382.670013  452610000   
1997-06-06   387.140015  387.220001  384.720001  384.989990  488940000   

                SP 500                                                 
                 Close        High         Low        Open     Volume  
Date                                                                   
1997-06-02  846.359985  851.340027  844.609985  848.280029  435950000  
1997-06-03  845.479980  850.559998  841.510010  846.359985  527120000  
1997-06-04  840.109985  845.549988  838.820007  845.479980  466690000  
1997-06-05  843.429993  848.890015  840.109985  840.109985  452610000  
1997-06-06  858.010010  859.239990  843.359985  843.429993  488940000

In [6]:
# px.line(price_data, width=1000)
price_data_px = price_data.xs('Close', level=1, axis=1)
px.line(price_data_px, width=1000)

In [7]:
short_window = 30
long_window = 100

signals_df = price_data.copy()

for col in signals_df.columns:

    col_name = col[0]

    signals_df[col_name, 'Actual Returns'] = (signals_df[col_name, 'Close'].pct_change())

    # Generate the fast and slow simple moving averages
    signals_df[col_name, 'SMA 30'] = signals_df[col_name, 'Close'].rolling(window=short_window).mean()
    signals_df[col_name, 'SMA 100'] = signals_df[col_name, 'Close'].rolling(window=long_window).mean()

    signals_df[col_name, 'DMAC Signal'] = 0.0
    signals_df[col_name, 'DMAC Signal'][short_window:] = np.where(
        signals_df[col_name, 'SMA 30'][short_window:] < signals_df[col_name, 'SMA 100'][short_window:], 1.0, 0.0
    )

    signals_df[col_name, 'DMAC Entry/Exit'] = signals_df[col_name, 'DMAC Signal'].diff()

signals_df = signals_df.sort_index(axis='columns')
signals_df.tail()

/var/folders/jh/1t34xq2s7f733bwqfjms9b6h0000gn/T/ipykernel_6255/2298007018.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/var/folders/jh/1t34xq2s7f733bwqfjms9b6h0000gn/T/ipykernel_6255/2298007018.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



NASDAQ 100                                            \
           Actual Returns         Close DMAC Entry/Exit DMAC Signal   
Date                                                                  
2022-05-24      -0.021974  11769.839844             0.0         1.0   
2022-05-25       0.014791  11943.929688             0.0         1.0   
2022-05-26       0.027869  12276.790039             0.0         1.0   
2022-05-27       0.032959  12681.419922             0.0         1.0   
2022-05-31      -0.003101  12642.099609             0.0         1.0   

                                                                    \
                    High           Low          Open       SMA 100   
Date                                                                 
2022-05-24  11842.809570  11576.110352  11807.780273  14097.154287   
2022-05-25  12028.889648  11714.269531  11732.450195  14053.392783   
2022-05-26  12337.730469  11901.870117  11906.830078  14011.142988   
2022-05-27  12682.580078  12405.290039  12421.799805  13975.159883   
2022-05-31  12762.839844  12482.320312  12688.950195  13943.863076   

                                      ...         SP 500               \
                  SMA 30      Volume  ... Actual Returns        Close   
Date                                  ...                               
2022-05-24  12914.523307  4706300000  ...      -0.008121  3941.479980   
2022-05-25  12847.979622  4500920000  ...       0.009451  3978.729980   
2022-05-26  12783.296289  4651470000  ...       0.019883  4057.840088   
2022-05-27  12742.903288  4774530000  ...       0.024742  4158.240234   
2022-05-31  12700.614616  6028940000  ...      -0.006274  4132.149902   

                                                                               \
           DMAC Entry/Exit DMAC Signal         High          Low         Open   
Date                                                                            
2022-05-24             0.0         1.0  3955.679932  3875.129883  3942.939941   
2022-05-25             0.0         1.0  3999.330078  3925.030029  3929.590088   
2022-05-26             0.0         1.0  4075.139893  3984.600098  3984.600098   
2022-05-27             0.0         1.0  4158.490234  4077.429932  4077.429932   
2022-05-31             0.0         1.0  4168.339844  4104.879883  4151.089844   

                                                  
                SMA 100       SMA 30      Volume  
Date                                              
2022-05-24  4378.717395  4160.357674  3901640000  
2022-05-25  4370.842893  4146.400334  4322190000  
2022-05-26  4363.455693  4133.442008  3961940000  
2022-05-27  4357.102695  4125.630355  3560560000  
2022-05-31  4351.418394  4116.979020  5192220000  

[5 rows x 30 columns]

In [12]:
ndq = signals_df['SP 500'].copy()
ndq = pd.concat([ndq, TA.MACD(signals_df['NASDAQ 100'])])

entry_markers = ndq[ndq['DMAC Entry/Exit'] == 1.0]['Close']
exit_markers = ndq[ndq['DMAC Entry/Exit'] == -1.0]['Close']

fig1 = px.line(ndq[['Close', 'SMA 30', 'SMA 100']])

fig2 = px.scatter(
    entry_markers, 
    x=entry_markers.index, 
    y='Close',
)
fig2.update_traces(
    marker=dict(
        color='green',
        size=15,
        line=dict(
                width=1,
                color='black'
            ),
        ),
    selector=dict(mode='markers')
)

fig3 = px.scatter(
    exit_markers,
    x=exit_markers.index, 
    y='Close',
    height=1000
)
fig3.update_traces(
    marker=dict(
        color='red',
        size=15,
        line=dict(
                width=1,
                color='black'
            ),
        ),
    selector=dict(mode='markers')
)

fig4 = go.Figure(data=fig1.data + fig2.data + fig3.data)
fig4.show()

In [9]:
px.line(ndq[['Close', 'MACD']])